<a href="https://colab.research.google.com/github/Kostratana/diplome_computer_vision_airport/blob/main/Keras_CV.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Keras_CV

In [ ]:
# корневой каталог подготовленного датасета дублируем на случай отдельного запуска
PREPAIRED_DATASET_PATH = '/content/dataset'

# гиперпараметры обучения
BATCH_SIZE = 16
LEARNING_RATE = 0.001
EPOCH = 20
GLOBAL_CLIPNORM = 10.0
BB_FORMAT = "xyxy"

In [ ]:
# @title Служебные функции для подготовки датасета

def bb_list_from_file(filepath):
    if BB_FORMAT == 'rel_xyxy':
        '''возвращает кортеж:
        список классов и список списков б-боксов,
        сконвертированных в формат rel_xyxy
        из файла аннотации в формате для йоло'''
        class_list = []
        bb_list = []
        with open(filepath) as fp:
            for i in fp.readlines():
                l = i.strip().split()
                class_list.append(int(l[0]))
                bb_list.append([round(float(l[1]) - float(l[3]) / 2, 6),
                                round(float(l[2]) - float(l[4]) / 2, 6),
                                round(float(l[1]) + float(l[3]) / 2, 6),
                                round(float(l[2]) + float(l[4]) / 2, 6)])

        return class_list, bb_list
    elif BB_FORMAT == 'xyxy':
        '''возвращает кортеж:
        список классов и список списков б-боксов,
        сконвертированных в формат xyxy
        из файла аннотации в формате для йоло'''
        width, height = 384, 950
        class_list = []
        bb_list = []
        with open(filepath) as fp:
            for i in fp.readlines():
                l = i.strip().split()
                class_list.append(int(l[0]))
                bb_list.append([int(round(width * (float(l[1]) - float(l[3]) / 2), 0)),
                                int(round(height * (float(l[2]) - float(l[4]) / 2), 0)),
                                int(round(width * (float(l[1]) + float(l[3]) / 2), 0)),
                                int(round(height * (float(l[2]) + float(l[4]) / 2), 0))])

        return class_list, bb_list

# список файлов изображений представляет собой простой список путей
# список классов содержит списки попавшихся классов из файла аннотации
# а список б-боксов - списки соответствующих б-боксов

# датасет заранее подготовлен и наборы файлов соответствуют друг другу,
# поэтому обходим их параллельно, не заморачиваясь на проверках
def parse_labels(path_images, path_labels):
    '''возвращает кортеж:
    список путей к изображениям, список классов, список б-боксов'''
    image_paths = sorted([os.path.join(path_images, f_name) for f_name in os.listdir(path_images)])
    bboxes = []
    classes = []
    for label_file in tqdm(sorted([os.path.join(path_labels, f_name) for f_name in os.listdir(path_labels)])):
        class_list, bb_list = bb_list_from_file(label_file)
        classes.append(class_list)
        bboxes.append(bb_list)

    return image_paths, classes, bboxes

In [ ]:
# единственный класс, задаем словарем
class_mapping = {0: 'danger'}

Данные 4 кода позволяют извлечь пути к изображениям, классы объектов на изображениях и ограничивающие рамки объектов для обучающего набора данных.

In [ ]:
train_image_paths, train_classes, train_bboxes = parse_labels('/content/dataset/train/images', '/content/dataset/train/labels')

  0%|          | 0/6054 [00:00<?, ?it/s]

In [ ]:
val_image_paths, val_classes, val_bboxes = parse_labels('/content/dataset/val/images', '/content/dataset/val/labels')

  0%|          | 0/1728 [00:00<?, ?it/s]

In [ ]:
test_image_paths, test_classes, test_bboxes = parse_labels('/content/dataset/test/images', '/content/dataset/test/labels')

  0%|          | 0/864 [00:00<?, ?it/s]

In [ ]:
test_2_image_paths, test_2_classes, test_2_bboxes = parse_labels('/content/dataset/test_2/images', '/content/dataset/test_2/labels')

  0%|          | 0/596 [00:00<?, ?it/s]

In [ ]:
# вариант из примера про yolo с созданием ragged тенсоров, т.к. количество
# классов и б-боксов на изображениях различно
t_train_bbox = tf.ragged.constant(train_bboxes, inner_shape=(4,))
t_train_classes = tf.ragged.constant(train_classes)
t_train_image_paths = tf.ragged.constant(train_image_paths)

# создание train датасета
train_data = tf.data.Dataset.from_tensor_slices((t_train_image_paths, t_train_classes, t_train_bbox))


t_val_bbox = tf.ragged.constant(val_bboxes, inner_shape=(4,))
t_val_classes = tf.ragged.constant(val_classes)
t_val_image_paths = tf.ragged.constant(val_image_paths)

# создание val датасета
val_data = tf.data.Dataset.from_tensor_slices((t_val_image_paths, t_val_classes, t_val_bbox))


t_test_bbox = tf.ragged.constant(test_bboxes, inner_shape=(4,))
t_test_classes = tf.ragged.constant(test_classes)
t_test_image_paths = tf.ragged.constant(test_image_paths)

# создание test датасета
test_data = tf.data.Dataset.from_tensor_slices((t_test_image_paths, t_test_classes, t_test_bbox))

In [ ]:
t_test_2_bbox = tf.ragged.constant(test_2_bboxes, inner_shape=(4,))
t_test_2_classes = tf.ragged.constant(test_2_classes)
t_test_2_image_paths = tf.ragged.constant(test_2_image_paths)

# создание test_2 датасета
test_2_data = tf.data.Dataset.from_tensor_slices((t_test_2_image_paths, t_test_2_classes, t_test_2_bbox))

In [ ]:
# проверка корректности тензора
display(t_train_bbox.shape)

TensorShape([6054, None, 4])

In [ ]:
# @title Служебные функции для сборки датасета из примера про yolo
def load_image(image_path):
    image = tf.io.read_file(image_path)
    # t_image = tf.image.decode_jpeg(image, channels=3)
    # tf.image.decode_ не работает с tif, замена
    # tfio.experimental.image.decode_tiff возвращает RGBA, отрезаем последний элемент
    t_image = tfio.experimental.image.decode_tiff(image)[:,:,:-1]

    return t_image


def load_dataset(image_path, classes, bbox):
    # Read Image
    image = load_image(image_path)
    bounding_boxes = {
        "classes": tf.cast(classes, dtype=tf.float32),
        "boxes": bbox,
    }
    return {"images": tf.cast(image, tf.float32), "bounding_boxes": bounding_boxes}

In [ ]:
# слой ресайзинга изображений в подходящий для сетки размер
image_resizing_to64 = keras_cv.layers.Resizing(
    640, 640,
    pad_to_aspect_ratio=True,
    bounding_box_format=BB_FORMAT
)

# подготовка изображений для подачи в предикт пример
# image_batch = image_resizing_to64([image])

Этот код позволяет подготовить и нарезать датасеты `train_data`, `val_data` и `test_data` для обучения, валидации и тестирования модели.

In [ ]:
# нарезка датасета
train_ds = train_data.map(load_dataset, num_parallel_calls=tf.data.AUTOTUNE)
train_ds = train_ds.shuffle(BATCH_SIZE * 4)

train_ds = train_ds.ragged_batch(BATCH_SIZE, drop_remainder=True)

val_ds = val_data.map(load_dataset, num_parallel_calls=tf.data.AUTOTUNE)
val_ds = val_ds.shuffle(BATCH_SIZE * 4)

val_ds = val_ds.ragged_batch(BATCH_SIZE, drop_remainder=True)
#val_ds = val_ds.ragged_batch(1, drop_remainder=True)

test_ds = test_data.map(load_dataset, num_parallel_calls=tf.data.AUTOTUNE)
test_ds = test_ds.ragged_batch(BATCH_SIZE, drop_remainder=True)

In [ ]:
# вариант из примера про yolo с созданием ragged тенсоров, т.к. количество
# классов и б-боксов на изображениях различно
t_train_bbox = tf.ragged.constant(train_bboxes, inner_shape=(4,))
t_train_classes = tf.ragged.constant(train_classes)
t_train_image_paths = tf.ragged.constant(train_image_paths)

# создание train датасета
train_data = tf.data.Dataset.from_tensor_slices((t_train_image_paths, t_train_classes, t_train_bbox))


t_val_bbox = tf.ragged.constant(val_bboxes, inner_shape=(4,))
t_val_classes = tf.ragged.constant(val_classes)
t_val_image_paths = tf.ragged.constant(val_image_paths)

# создание val датасета
val_data = tf.data.Dataset.from_tensor_slices((t_val_image_paths, t_val_classes, t_val_bbox))


t_test_bbox = tf.ragged.constant(test_bboxes, inner_shape=(4,))
t_test_classes = tf.ragged.constant(test_classes)
t_test_image_paths = tf.ragged.constant(test_image_paths)

# создание test датасета
test_data = tf.data.Dataset.from_tensor_slices((t_test_image_paths, t_test_classes, t_test_bbox))

In [ ]:
t_test_2_bbox = tf.ragged.constant(test_2_bboxes, inner_shape=(4,))
t_test_2_classes = tf.ragged.constant(test_2_classes)
t_test_2_image_paths = tf.ragged.constant(test_2_image_paths)

# создание test_2 датасета
test_2_data = tf.data.Dataset.from_tensor_slices((t_test_2_image_paths, t_test_2_classes, t_test_2_bbox))

In [ ]:
# проверка корректности тензора
display(t_train_bbox.shape)

TensorShape([6054, None, 4])

In [ ]:
# @title Служебные функции для сборки датасета из примера про yolo
def load_image(image_path):
    image = tf.io.read_file(image_path)
    # t_image = tf.image.decode_jpeg(image, channels=3)
    # tf.image.decode_ не работает с tif, замена
    # tfio.experimental.image.decode_tiff возвращает RGBA, отрезаем последний элемент
    t_image = tfio.experimental.image.decode_tiff(image)[:,:,:-1]

    return t_image


def load_dataset(image_path, classes, bbox):
    # Read Image
    image = load_image(image_path)
    bounding_boxes = {
        "classes": tf.cast(classes, dtype=tf.float32),
        "boxes": bbox,
    }
    return {"images": tf.cast(image, tf.float32), "bounding_boxes": bounding_boxes}

In [ ]:
# слой ресайзинга изображений в подходящий для сетки размер
image_resizing_to64 = keras_cv.layers.Resizing(
    640, 640,
    pad_to_aspect_ratio=True,
    bounding_box_format=BB_FORMAT
)

# подготовка изображений для подачи в предикт пример
# image_batch = image_resizing_to64([image])

In [ ]:
# нарезка датасета
train_ds = train_data.map(load_dataset, num_parallel_calls=tf.data.AUTOTUNE)
train_ds = train_ds.shuffle(BATCH_SIZE * 4)

train_ds = train_ds.ragged_batch(BATCH_SIZE, drop_remainder=True)

val_ds = val_data.map(load_dataset, num_parallel_calls=tf.data.AUTOTUNE)
val_ds = val_ds.shuffle(BATCH_SIZE * 4)

val_ds = val_ds.ragged_batch(BATCH_SIZE, drop_remainder=True)
#val_ds = val_ds.ragged_batch(1, drop_remainder=True)

test_ds = test_data.map(load_dataset, num_parallel_calls=tf.data.AUTOTUNE)
test_ds = test_ds.ragged_batch(BATCH_SIZE, drop_remainder=True)

In [ ]:
test_2_ds = test_2_data.map(load_dataset, num_parallel_calls=tf.data.AUTOTUNE)
test_2_ds = test_2_ds.ragged_batch(len(test_2_ds), drop_remainder=True)

In [ ]:
test_2_ds = test_2_data.map(load_dataset, num_parallel_calls=tf.data.AUTOTUNE)
test_2_ds = test_2_ds.ragged_batch(len(test_2_ds), drop_remainder=True)

In [ ]:
# @title Служебные функции для визуализации датасета из примера про yolo
def visualize_dataset(inputs, value_range, rows, cols, bounding_box_format):
    inputs = next(iter(inputs.take(1)))
    images, bounding_boxes = inputs["images"], inputs["bounding_boxes"]
    # images, bounding_boxes = inputs[0], inputs[1]
    visualization.plot_bounding_box_gallery(
        images,
        value_range=value_range,
        rows=rows,
        cols=cols,
        y_true=bounding_boxes,
        scale=8,
        font_scale=0.7,
        bounding_box_format=bounding_box_format,
        class_mapping=class_mapping,
    )

In [ ]:
visualize_dataset(
    train_ds, bounding_box_format=BB_FORMAT, value_range=(0, 255), rows=3, cols=5
)

In [ ]:
visualize_dataset(
    test_2_ds, bounding_box_format=BB_FORMAT, value_range=(0, 255), rows=3, cols=5
)

Эта функция выполняет изменение размера изображений в наборе данных до размера 64x64 пикселя с помощью функции image_resizing_to64. Таким образом, все изображения в обучающем и валидационном наборах данных будут изменены до одинакового размера 64x64 пикселя. Это может быть полезно для стандартизации размеров изображений перед подачей их на вход нейронной сети для обучения, что поможет улучшить процесс обучения и повысить качество модели.

In [ ]:
# ресайз в размер для сетки
train_ds = train_ds.map(image_resizing_to64, num_parallel_calls=tf.data.AUTOTUNE)
val_ds = val_ds.map(image_resizing_to64, num_parallel_calls=tf.data.AUTOTUNE)

In [ ]:
test_3_ds =test_2_ds.map(image_resizing_to64, num_parallel_calls=tf.data.AUTOTUNE)

In [ ]:
# преобразование дс в кортеж для подачи в сетку
def dict_to_tuple(inputs):
    # return inputs["images"], inputs["bounding_boxes"]
    return inputs["images"], bounding_box.to_dense(
        inputs["bounding_boxes"], max_boxes=32
    )

train_ds = train_ds.map(dict_to_tuple, num_parallel_calls=tf.data.AUTOTUNE)
train_ds = train_ds.prefetch(tf.data.AUTOTUNE)

val_ds = val_ds.map(dict_to_tuple, num_parallel_calls=tf.data.AUTOTUNE)
val_ds = val_ds.prefetch(tf.data.AUTOTUNE)

In [ ]:
test_3_ds = test_3_ds.map(dict_to_tuple, num_parallel_calls=tf.data.AUTOTUNE)
test_3_ds = test_3_ds.prefetch(tf.data.AUTOTUNE)

In [ ]:
backbone = keras_cv.models.YOLOV8Backbone.from_preset('yolo_v8_xs_backbone_coco', load_weights=True)

In [ ]:
yolo = keras_cv.models.YOLOV8Detector(
    num_classes= len(class_mapping),
    bounding_box_format=BB_FORMAT,
    backbone=backbone,
    fpn_depth=3,
)

yolo.summary()

In [ ]:
optimizer = tf.keras.optimizers.Adam(
    learning_rate=LEARNING_RATE,
    global_clipnorm=GLOBAL_CLIPNORM,
)

yolo.compile(
    optimizer=optimizer, classification_loss='binary_crossentropy', box_loss='ciou'
)

In [ ]:
class EvaluateCOCOMetricsCallback(keras.callbacks.Callback):
    def __init__(self, data, save_path):
        super().__init__()
        self.data = data
        self.metrics = keras_cv.metrics.BoxCOCOMetrics(
            bounding_box_format=BB_FORMAT,
            evaluate_freq=1e9,
        )

        self.save_path = save_path
        self.best_map = -1.0

    def on_epoch_end(self, epoch, logs):
        self.metrics.reset_state()
        for batch in self.data:
            images, y_true = batch[0], batch[1]
            y_pred = self.model.predict(images, verbose=0)
            self.metrics.update_state(y_true, y_pred)

        metrics = self.metrics.result(force=True)
        logs.update(metrics)

        current_map = metrics['MaP']
        if current_map > self.best_map:
            self.best_map = current_map
            self.model.save(self.save_path)  # Сохранение модели если mAP улучшился

        return logs

In [ ]:
from tensorflow.keras.layers import Dropout, Flatten, Dense
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import ConvLSTM2D

class My_ConvLSTM_Model:
    def __init__(self, tensor_shape):
        self.model = Sequential()
        self.model.add(ConvLSTM2D(filters=64, kernel_size=(3, 3), input_shape=(None, 100, 10, 1)))  # Update input_shape here
        self.model.add(Dropout(0.2))
        self.model.add(Flatten())
        self.model.add(Dense(256, activation='relu'))
        self.model.add(Dropout(0.3))
        self.model.add(Dense(6, activation='softmax'))

# Define the input shape
tensor_shape = (None, 100, 10, 1)

# Create an instance of the model
model = My_ConvLSTM_Model(tensor_shape)


In [ ]:
# keras_cv.metrics.BoxCOCOMetrics поломали, замена другим набором
from keras_cv.callbacks import PyCOCOCallback



#

callbacks = [
    # keras.callbacks.ReduceLROnPlateau(patience=5),
    # keras.callbacks.EarlyStopping(patience=10),
    # keras.callbacks.ModelCheckpoint('weights.h5', save_weights_only=True),
    # Temporarily need PyCOCOCallback to verify
    # a 1:1 comparison with the PyMetrics version.
    # Currently, results do not match. I have a feeling this is due
    # to how we are creating the boxes in `BoxCOCOMetrics`
    PyCOCOCallback(val_ds, bounding_box_format=BB_FORMAT),
    # keras.callbacks.TensorBoard(log_dir=FLAGS.tensorboard_path),
]

In [ ]:
# обучение
yolo.fit(
    train_ds,
    validation_data=val_ds,
    epochs=3,
    # callbacks=[EvaluateCOCOMetricsCallback(val_ds, 'model.h5')], # наш callback
    # callbacks=callbacks, # наш callback
)

In [ ]:
prediction_decoder = keras_cv.layers.MultiClassNonMaxSuppression(
    bounding_box_format=BB_FORMAT,
    from_logits=True,
    # Decrease the required threshold to make predictions get pruned out
    iou_threshold=0.2,
    # Tune confidence threshold for predictions to pass NMS
    confidence_threshold=0.3,
)
yolo.prediction_decoder = prediction_decoder

NameError: name 'keras_cv' is not defined

In [ ]:
# визуализация
def visualize_detections(model, dataset, rows, cols, bounding_box_format):
    inputs = next(iter(dataset.take(1)))
    images, y_true = inputs[0], inputs[1]
    # images, y_true = inputs['images'], inputs['bounding_boxes']
    y_pred = model.predict(images)
    y_pred = bounding_box.to_ragged(y_pred)
    visualization.plot_bounding_box_gallery(
        images,
        value_range=(0, 255),
        bounding_box_format=bounding_box_format,
        y_true=y_true,
        y_pred=y_pred,
        scale=8,
        rows=rows,
        cols=cols,
        show=True,
        font_scale=0.7,
        class_mapping=class_mapping,
    )


visualize_detections(yolo, dataset=test_3_ds, rows=3, cols=5, bounding_box_format=BB_FORMAT)

In [ ]:
yolo.load_weights('/content/drive/MyDrive/test_4_scr_sys/cv-yolo/model.keras')

In [ ]:
for batch in val_ds:
        images, y_true = batch[0], batch[1]
        y_pred = yolo.predict(images, verbose=0)

In [ ]:
for batch in test_3_ds:
        images, y_true = batch[0], batch[1]
        # images, y_true = inputs['images'], inputs['bounding_boxes']
        y_pred = yolo.predict(images, verbose=0)